# 构建模型示例
1. 省略了读取config相关代码（在../Segmentation.py Segmentation3D的BuildSegModel中有读取参数+构建模型的全部过程）

## 引入相关库文件

In [1]:
import os
import sys
import six
import glob
import math
import pandas as pd
import numpy as np
from keras.utils import to_categorical
import scipy.ndimage as nd
from scipy.ndimage import zoom
import random

Using TensorFlow backend.


In [2]:
import keras
import tensorflow as tf
from keras import Model
from keras import backend as K
from keras.regularizers import l2
from keras.engine import Layer,InputSpec
from keras.layers.merge import concatenate
from keras.callbacks import TensorBoard,Callback
from keras.layers.advanced_activations import LeakyReLU
from keras.preprocessing.image import ImageDataGenerator
from keras.layers.normalization import BatchNormalization
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau
from keras import initializers, regularizers, constraints,optimizers
from keras.callbacks import ModelCheckpoint, LearningRateScheduler,TensorBoard
from keras.layers import Add,Input,Conv3D,Convolution3D,Dropout,UpSampling3D,Concatenate,MaxPooling3D,\
GlobalAveragePooling3D,Dense,GlobalMaxPooling3D,Lambda,Activation,Reshape,Permute, PReLU, Deconvolution3D,Multiply,GlobalAveragePooling3D,Dense

## 引入相关模型文件

In [3]:
sys.path.append('./backbones/')
sys.path.append('./baseLayers/')
from ResNet import Resnet3DBuilder
from VGGmodel import VGG
from NoduleSegEncoder import NoduleSegEncoder_proxima
from InstanceNorm import InstanceNormalization

In [4]:
sys.path.append('./decoders/')
from NoduleSegDecoder import NoduleSegDecoder_proxima

In [5]:
from modelBuild import build_model

# 参数定义

## 定义共用参数

In [18]:
num_blocks = 5
strides = [1,2,2,2,2]
nodule_seg_strides = [1,2,2,2,2]
atrous_rates = [1,1,1,1,1]
base_filters = 32
norm_func = InstanceNormalization
activation_func = LeakyReLU
kernel_size = 3
padding = 'same'
dropout_rate = 0.5
input_shape = (32,64,64,1)
num_classes = 1
kernel_initializer = 'he_normal'
kernel_regularizer = None   

## 定义每一个模型的参数

# VGG的参数

In [14]:
parameter_list = {
    'num_blocks':num_blocks,
    'strides':strides,
    'atrous_rates':atrous_rates,
    'base_filters':base_filters,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'dropout_rate':dropout_rate,
    'num_classes':num_classes,
    'classification_layers':GlobalMaxPooling3D
}

In [15]:
resnet_parameter_list = {
    'base_filters':base_filters,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'dropout_rate':dropout_rate,
    'num_classes':num_classes,
    'classification_layers':GlobalMaxPooling3D,
    'init_kernel_size':1
}

In [17]:
noduleseg_parameter_list = {
    'num_blocks':num_blocks,
    'strides':nodule_seg_strides,
    'atrous_rates':atrous_rates,
    'base_filters':base_filters,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'dropout_rate':dropout_rate,
    'num_classes':num_classes,
    'classification_layers':GlobalMaxPooling3D
}

In [10]:
noduleseg_decoder_parameter_list = {
   'kernel_initializer':kernel_initializer,
    'kernel_regularizer':kernel_regularizer,
    'kernel_size':kernel_size,
    'final_kernel_size':1,
    'norm_func':norm_func,
    'activation_func':activation_func,
    'kernel_size':kernel_size,
    'padding':padding,
    'seg_num_class':1,
    'merge_axis':-1,
    'SEB_choice':True,
    'ACR_choice':False,
    'OCR_choice':False,
    'deep_supervision':True,
    'num_units':[3,3,3,3],
    'aux_task':False,
     u'densityTypeConvertMap': 
        {u'1': 1,
          u'2': 2,
          u'3': 3,
          u'4': 4,
          u'5': 1,
          u'6': 4},
    u'num_classes': num_classes
    
    
    
}

## 将各个模型的参数放到字典中，根据名字提取参数

In [11]:
model_parameter_list = {
    "NoduleSegDecoder_proxima":noduleseg_decoder_parameter_list,
    "NoduleSegEncoder_proxima":noduleseg_parameter_list,
    "VGG":parameter_list,
    "Res":resnet_parameter_list
    
    
}

# 可能的encoder有：
    NoduleSegEncoder_proxima（结节分割encoder）
    Res(resnet,目前调用形式仍需改写)
    VGG(VGG)


# 可能的decoder：
    NoduleSegDecoder_proxima

In [12]:
for encoder_name in ['NoduleSegEncoder_proxima','Res','VGG']:
    encoder_parameter_list = model_parameter_list[encoder_name]
    encoder_result = build_model(encoder_name,input_shape,parameter_list=[encoder_parameter_list])
    for decoder_name in ['NoduleSegDecoder_proxima']:
        print ('='*60)
        print ('Encoder is %s, decoder is %s'%(encoder_name,decoder_name))
        decoder_parameter_list = model_parameter_list[decoder_name]
        model = build_model(decoder_name,input_shape,[encoder_result,decoder_parameter_list])
        model.summary()

Encoder is NoduleSegEncoder_proxima, decoder is NoduleSegDecoder_proxima


decoders/NoduleSegDecoder.py:54: UserWarning: Update your `Conv3D` call to the Keras 2 API: `Conv3D(kernel_initializer="he_normal", name="NoduleSegDecoder_Block01_conv", activation=None, padding="same", kernel_regularizer=<keras.reg..., filters=256, kernel_size=3)`
  border_mode=padding,activation=current_acti,name='%s_conv'%block_pre)(x)
decoders/NoduleSegDecoder.py:54: UserWarning: Update your `Conv3D` call to the Keras 2 API: `Conv3D(kernel_initializer="he_normal", name="NoduleSegDecoder_Block02_conv", activation=None, padding="same", kernel_regularizer=<keras.reg..., filters=128, kernel_size=3)`
  border_mode=padding,activation=current_acti,name='%s_conv'%block_pre)(x)
decoders/NoduleSegDecoder.py:54: UserWarning: Update your `Conv3D` call to the Keras 2 API: `Conv3D(kernel_initializer="he_normal", name="NoduleSegDecoder_Block03_conv", activation=None, padding="same", kernel_regularizer=<keras.reg..., filters=64, kernel_size=3)`
  border_mode=padding,activation=current_acti,name='%

__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 32, 64, 64, 1 0                                            
__________________________________________________________________________________________________
NoduleSegConvBlock01_conv_01 (C (None, 32, 64, 64, 3 896         input_1[0][0]                    
__________________________________________________________________________________________________
NoduleSegConvBlock01_norm_01 (I (None, 32, 64, 64, 3 2           NoduleSegConvBlock01_conv_01[0][0
__________________________________________________________________________________________________
NoduleSegConvBlock01_activation (None, 32, 64, 64, 3 0           NoduleSegConvBlock01_norm_01[0][0
__________________________________________________________________________________________________
NoduleSegC

Encoder is Res, decoder is NoduleSegDecoder_proxima
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_2 (InputLayer)            (None, 32, 64, 64, 1 0                                            
__________________________________________________________________________________________________
ResNet_InitBlock_conv_01 (Conv3 (None, 32, 64, 64, 3 64          input_2[0][0]                    
__________________________________________________________________________________________________
ResNet_InitBlock_norm_01 (Insta (None, 32, 64, 64, 3 2           ResNet_InitBlock_conv_01[0][0]   
__________________________________________________________________________________________________
ResNet_InitBlock_activation_01  (None, 32, 64, 64, 3 0           ResNet_InitBlock_norm_01[0][0]   
_________________________________________________________

Encoder is VGG, decoder is NoduleSegDecoder_proxima
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_3 (InputLayer)            (None, 32, 64, 64, 1 0                                            
__________________________________________________________________________________________________
VGG_block01_conv_01 (Conv3D)    (None, 32, 64, 64, 3 896         input_3[0][0]                    
__________________________________________________________________________________________________
VGG_block01_norm_01 (InstanceNo (None, 32, 64, 64, 3 2           VGG_block01_conv_01[0][0]        
__________________________________________________________________________________________________
VGG_block01_activation_01 (Leak (None, 32, 64, 64, 3 0           VGG_block01_norm_01[0][0]        
_________________________________________________________